In [1]:
import geopandas as gpd
import pandas as pd
import datetime
import numpy as np
import matplotlib.pyplot as plt
from shapely.geometry import LineString, Point
import math
from shapely.affinity import translate
from shapely.geometry import Polygon

/usr/local/lib/python3.8/dist-packages/geopandas/_compat.py:123: UserWarning: The Shapely GEOS version (3.10.3-CAPI-1.16.1) is incompatible with the GEOS version PyGEOS was compiled with (3.9.1-CAPI-1.14.2). Conversions between both will be slow.
  warnings.warn(


In [2]:
df = gpd.read_file('Shapefiles/OhaweBeach_intersects.shp')
df.crs = 2193
df

OBJECTID  TransectID  TransOrder  BaselineID  ShorelineI   Distance  \
0            1           1           1           1  08/05/1951  15.261085   
1            2           1           1           1  28/08/1972  16.499539   
2            3           1           1           1  19/03/2017  11.448243   
3            4           2           2           1  08/05/1951  16.006630   
4            5           2           2           1  28/08/1972  17.954045   
...        ...         ...         ...         ...         ...        ...   
5295      5398         897         897           1  30/12/2009  17.875030   
5296      5399         897         897           1  19/03/2017  16.096489   
5297      5400         898         898           1  02/09/2003  15.292746   
5298      5401         898         898           1  30/12/2009  18.682005   
5299      5402         898         898           1  19/03/2017  14.861966   

        IntersectX    IntersectY  Uncertaint  Code  \
0     1.695399e+06  5.618558e+06    3.203576     2   
1     1.695399e+06  5.618556e+06    3.472650     2   
2     1.695400e+06  5.618561e+06    2.396623     2   
3     1.695409e+06  5.618558e+06    3.203576     2   
4     1.695409e+06  5.618556e+06    3.472650     2   
...            ...           ...         ...   ...   
5295  1.703997e+06  5.616813e+06    2.429774     2   
5296  1.703998e+06  5.616815e+06    2.396623     2   
5297  1.704008e+06  5.616812e+06    2.452305     2   
5298  1.704007e+06  5.616809e+06    2.429774     2   
5299  1.704008e+06  5.616812e+06    2.396623     2   

                             geometry  
0     POINT (1695399.271 5618557.671)  
1     POINT (1695399.166 5618556.437)  
2     POINT (1695399.595 5618561.470)  
3     POINT (1695409.018 5618557.575)  
4     POINT (1695408.832 5618555.637)  
...                               ...  
5295  POINT (1703997.363 5616812.899)  
5296  POINT (1703998.095 5616814.520)  
5297  POINT (1704008.263 5616811.868)  
5298  POINT (1704006.950 5616808.743)  
5299  POINT (1704008.430 5616812.265)  

[5300 rows x 11 columns]

In [3]:
BASE_YEAR = 1940
FUTURE_YEAR = 2100
df['Date'] = pd.to_datetime(df.ShorelineI, dayfirst=True)
df["Year"] = df.Date.dt.year
df['YearsSinceBase'] = (df.Date - pd.Timestamp(BASE_YEAR, 1, 1)).dt.days / 365.25
df['YearsUntilFuture'] = (pd.Timestamp(FUTURE_YEAR, 1, 1) - df.Date).dt.days / 365.25
df.Date = df.Date.astype(str)
df

OBJECTID  TransectID  TransOrder  BaselineID  ShorelineI   Distance  \
0            1           1           1           1  08/05/1951  15.261085   
1            2           1           1           1  28/08/1972  16.499539   
2            3           1           1           1  19/03/2017  11.448243   
3            4           2           2           1  08/05/1951  16.006630   
4            5           2           2           1  28/08/1972  17.954045   
...        ...         ...         ...         ...         ...        ...   
5295      5398         897         897           1  30/12/2009  17.875030   
5296      5399         897         897           1  19/03/2017  16.096489   
5297      5400         898         898           1  02/09/2003  15.292746   
5298      5401         898         898           1  30/12/2009  18.682005   
5299      5402         898         898           1  19/03/2017  14.861966   

        IntersectX    IntersectY  Uncertaint  Code  \
0     1.695399e+06  5.618558e+06    3.203576     2   
1     1.695399e+06  5.618556e+06    3.472650     2   
2     1.695400e+06  5.618561e+06    2.396623     2   
3     1.695409e+06  5.618558e+06    3.203576     2   
4     1.695409e+06  5.618556e+06    3.472650     2   
...            ...           ...         ...   ...   
5295  1.703997e+06  5.616813e+06    2.429774     2   
5296  1.703998e+06  5.616815e+06    2.396623     2   
5297  1.704008e+06  5.616812e+06    2.452305     2   
5298  1.704007e+06  5.616809e+06    2.429774     2   
5299  1.704008e+06  5.616812e+06    2.396623     2   

                             geometry        Date  Year  YearsSinceBase  \
0     POINT (1695399.271 5618557.671)  1951-05-08  1951       11.348392   
1     POINT (1695399.166 5618556.437)  1972-08-28  1972       32.657084   
2     POINT (1695399.595 5618561.470)  2017-03-19  2017       77.212868   
3     POINT (1695409.018 5618557.575)  1951-05-08  1951       11.348392   
4     POINT (1695408.832 5618555.637)  1972-08-28  1972       32.657084   
...                               ...         ...   ...             ...   
5295  POINT (1703997.363 5616812.899)  2009-12-30  2009       69.995893   
5296  POINT (1703998.095 5616814.520)  2017-03-19  2017       77.212868   
5297  POINT (1704008.263 5616811.868)  2003-09-02  2003       63.668720   
5298  POINT (1704006.950 5616808.743)  2009-12-30  2009       69.995893   
5299  POINT (1704008.430 5616812.265)  2017-03-19  2017       77.212868   

      YearsUntilFuture  
0           148.651608  
1           127.342916  
2            82.787132  
3           148.651608  
4           127.342916  
...                ...  
5295         90.004107  
5296         82.787132  
5297         96.331280  
5298         90.004107  
5299         82.787132  

[5300 rows x 15 columns]

In [4]:
lines_shapefile = 'Shapefiles/OhaweBeach_TransectLines.shp'
TransectLine = gpd.read_file(lines_shapefile)
TransectLine.set_index("TransectID", inplace=True)
azimuth_lookup = TransectLine.Azimuth.to_dict()

In [5]:
def calculate_new_coordinates(old_x, old_y, bearing, distance):
    bearing_radians = math.radians(bearing)
    new_x = old_x + (distance * math.sin(bearing_radians))
    new_y = old_y + (distance * math.cos(bearing_radians))
    return Point(new_x, new_y)

In [10]:
def predict(df, model="linear"):
    grouped = df.groupby('TransectID')
    results = []
    for group_name, group_data in grouped:
        if group_name not in azimuth_lookup.keys():
            continue
        coefficients = np.polyfit(group_data.YearsSinceBase, group_data.Distance, 1)
        slope = coefficients[0]
        intercept = coefficients[1]
        # Erosion only
        if slope < 0:
            predicted_distance = slope * (FUTURE_YEAR - BASE_YEAR) + intercept
            latest_row = group_data[group_data.Date == group_data['Date'].max()].iloc[0]
            distance_difference = latest_row.Distance - predicted_distance
            results.append({
                "TransectID": group_name,
                "Year": FUTURE_YEAR,
                "Distance": predicted_distance,
                "geometry": calculate_new_coordinates(latest_row.geometry.x, latest_row.geometry.y, azimuth_lookup[group_name], distance_difference),
                "ocean_point": calculate_new_coordinates(latest_row.geometry.x, latest_row.geometry.y, azimuth_lookup[group_name] + 180, 500)
            })
    results = gpd.GeoDataFrame(results, crs=2193)
    return results

results = predict(df)
results

TransectID  Year   Distance                         geometry  \
0             1  2100   6.465705  POINT (1695400.018 5618566.434)   
1             2  2100   5.188576  POINT (1695410.052 5618568.344)   
2             3  2100   1.118642  POINT (1695420.404 5618573.028)   
3             4  2100   3.748464  POINT (1695429.987 5618570.751)   
4             5  2100  -0.323935  POINT (1695440.569 5618575.069)   
..          ...   ...        ...                              ...   
845         894  2100 -12.789309  POINT (1703983.771 5616852.786)   
846         895  2100  -8.813090  POINT (1703990.061 5616843.688)   
847         896  2100  -7.387554  POINT (1703998.415 5616838.640)   
848         897  2100  -5.705785  POINT (1704007.067 5616834.390)   
849         898  2100  12.385645  POINT (1704009.389 5616814.548)   

                                       ocean_point  
0      POINT (1695357.1476834903 5618063.27499578)  
1     POINT (1695361.6286028617 5618064.522638125)  
2      POINT (1695364.413578569 5618065.057570531)  
3     POINT (1695357.2567212773 5618067.281149226)  
4      POINT (1695360.312163207 5618068.918672596)  
..                                             ...  
845   POINT (1703735.031977878 5616384.9764303835)  
846   POINT (1703748.9295986379 5616375.703378054)  
847     POINT (1703765.1385902108 5616368.7069437)  
848  POINT (1703792.3379116538 5616358.8178834915)  
849   POINT (1703814.7526662578 5616351.299643388)  

[850 rows x 5 columns]

In [7]:
pd.concat([df, results.drop(columns="ocean_point")]).explore("Year")

In [8]:
polygon = Polygon([*list(results.geometry), *list(results.ocean_point)[::-1]])
polygon = gpd.GeoSeries(polygon, crs=2193)
polygon.explore()

In [9]:
output_shapefile = "Projected_Shoreline_Polygons/OhaweBeach_linear.shp"
polygon.to_file(output_shapefile, driver="ESRI Shapefile")